In [33]:
import pandas as pd
import numpy as np
import logging, os
import re
import boto3
import sys
import pickle
import random
import tensorflow as tf
from tensorflow import keras
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense, LSTM, Dropout
from tensorflow.keras.optimizers import RMSprop
from tensorflow.keras.callbacks import LambdaCallback

In [11]:
left_tweets = pd.read_csv('../data/left_tweets.csv')
left_tweets.tweets

0         @nprpolitics Do you think Consigliere Barr can...
1         @realDonaldTrump @seanhannity @FoxNews I wonde...
2         @WhiteHouse @realDonaldTrump I wonder how MANY...
3         @WhiteHouse @realDonaldTrump I wonder how MANY...
4         @realDonaldTrump @seanhannity @FoxNews Hey @re...
                                ...                        
236874    INCITING WHITE SUPREMACIST VIOLENCE\n\nTORTURI...
236875    Congrats @RebeccaforWA on reaching 40,000 foll...
236876    Just saw this tweet.\n\nWow.\n\nThere are some...
236877    ENOUGH LAWLESS BEHAVIOR!!\n\nMurdering black p...
236878    FOR YOU\n\nI improvised this piano meditation ...
Name: tweets, Length: 236879, dtype: object

In [28]:
tweet_list = []
for tweet in left_tweets.tweets:
    if isinstance(tweet,str):
        print(tweet[:10])
        if tweet[:1] != '@':
            tweet_list.append(tweet)

@nprpoliti
@realDonal
@WhiteHous
@WhiteHous
@realDonal
@maggieNYT
@WhiteHous
Who ELSE i
@WhiteHous
@AmandiOnA
@gtconway3
@WhiteHous
@MeetThePr
@markknoll
@WhiteHous
@WhiteHous
Hey @realD
@WhiteHous
@mkraju Wh
@TeresaSha
@GOPChairw
The Secret
@WhiteHous
@GOPChairw
@JoeBiden 
@WhiteHous
@JoeBiden 
@realDonal
@JoeBiden 
@JoeBiden 
@CBSNews @
@mkraju Th
@Lawrence 
@mkraju Th
@luvmyRRs 
@TheRickWi
Hey Look K
@IvankaTru
@kylegriff
The Secret
@maggieNYT
For Once t
TRUMP 2020
@realDonal
TRUMP 2020
@realDonal
@alexnazar
@realDonal
@realDonal
OFF to INF
THIS is a 
@JWeber988
THIS is a 
THIS is a 
@realDonal
@realDonal
THIS is a 
@realDonal
Who ELSE i
@realDonal
@realDonal
@realDonal
@secupp An
Ironic isn
@realTuckF
@MollyJong
@GavinNews
@weijia Wh
Who ELSE i
@realDonal
@MSNBC Who
@AlanCavan
@AlanCavan
Anyone who
@GeoffRBen
Who ELSE i
@realDonal
@Laurie_Ga
@ABCPoliti
@MSNBC @Ma
@IngrahamA
Ironic isn
@GOPChairw
@davidalim
I keep REC
@itsJeffTi
@Politicus
@maggieNYT
“COWARD” h
Says the “
Seems like

@god7steve
@god7steve
@PeaEye1 m
@_DevilDog
@TheUnited
@Dhagash90
@Dhagash90
@Dhagash90
@Lambach @
@truthspea
@truthspea
@truthspea
@MarkHMeye
@MarkHMeye
@MarkHMeye
@MarkHMeye
@MarkHMeye
@MarkHMeye
@MarkHMeye
@MarkHMeye
@MarkHMeye
@truthspea
@truthspea
@truthspea
@howdyfrie
@Dhagash90
@Dhagash90
@Dhagash90
@MarkHMeye
@MarkHMeye
@MarkHMeye
@MarkHMeye
@howdyfrie
@howdyfrie
@howdyfrie
@howdyfrie
@MarkHMeye
@MarkHMeye
@MarkHMeye
@MarkHMeye
@neuralcul
@NickAdams
No matter 
The countr
Trump is d
lol @DeAnn
@HoarseWis
@DeAnna4Co
@yashar 🤔🤔
@yashar ye
This was c
@4tds_bund
@neuralcul
This would
@RVAwonk @
@realDonal
@RVAwonk @
The Presid
@tannenbau
@tannenbau
@RVAwonk @
White supr
@RVAwonk @
@RVAwonk @
@RVAwonk @
@JoshuaHol
@realDonal
There are 
Hoooly shi
@LewisForM
@_sourceE 
Where does
@realDonal
@realDonal
@LLRoberts
@lukeobrie
@mattgaetz
@realDonal
It's not r
Really...

A few cops
@WajahatAl
@RVAwonk I
At the sam
I sent thi
In case yo
!!!!!!!!!!
@RadioFree
@WFKARS Wr
@andrewkim
@jsolomonR

@daveweige
@MaryMargO
@SexCounse
@realDonal
@Rocman30 
@BarbMcQua
@TARAxBELL
@CarmineSa
@realDonal
@jacobson_
@bibi14287
@Acyn More
@Rocman30 
@KimberlyE
@StarTribu
@mkraju Re
@Rocman30 
@JakeSherm
@tennbaseb
@dantehman
@tress777 
@Eugene_Sc
@sanaayesh
@dailybles
@CarmineSa
@realDonal
@neal_katy
@nprpoliti
@thehill F
@MusingDav
@MusingDav
@JackBurto
@GreggPasc
@GreggPasc
@GreggPasc
@realDonal
@JackBurto
@Marty2613
@MarshaKim
@MarkDice 
@JayInslee
@AdamInHTo
@jimsciutt
@CillizzaC
@realDonal
@realDonal
@realDonal
@MSN @John
@Jenny_IDL
@Jenny_IDL
@RealCanda
@realDonal
@CryptoSno
@opsoctobe
@dnps1970 
@realDonal
@TheRightM
@realDonal
@realDonal
@realDonal
@t_rexSF49
@dave_brow
@dave_brow
@tedcruz T
@kylegriff
@realDonal
@JohnHaver
@bfugs22 @
@Slo_D @Ci
@Slo_D @Ci
@thehill W
@lsink69_l
@futbolnom
@RobinEnoc
@amandacar
@SethAbram
@Lynn96481
@GaiaRicha
@nprpoliti
@RobHerrin
@mustangwe
@jeffmason
@Yamiche T
@icecube B
@realDonal
@realDonal
@Slo_D @Ci
@Slo_D @Ci
@AHurst927
@Adamant_A
@NASCAR Ra

"Under sie
I am grate
.@realDona
@Manny_Fun
History of
How much m
"Trump is 
2/2 #COVID
1/2 #COVID
If you, li
@DuckDuckG
Everybody,
@thedjdaf 
@marcmaxme
@GOPLeader
@RepTerriS
3/3 I thin
2/3 I also
1/3 I agre
GOP SAYS p
@marcmaxme
@marcmaxme
@marcmaxme
@marcmaxme
@marcmaxme
@marcmaxme
"How many 
@Mrfirefig
I have the
#trumpIsDa
@CNN @Cher
@CNN @Cher
Whoa! This
@DrJasonJo
@marcmaxme
6/6  #COVI
5/6 #COVID
4/6 #COVID
3/6 #COVID
2/6 #COVID
1/6 #COVID
@GovInslee
@Turnip202
Angry Prot
The GOP Se
@VictoriaB
@Yamiche @
@CapehartJ
Research i
"Some indi
The counti
I think th
@butterwis
@HouseGOP 
So far, I 
@smartdiss
@AngelaBel
I missed t
@SummerFor
@sxdoc @St
@JoyAnnRei
.@Twitter:
trump is g
@TheDemocr
@nudog71 T
.@SpeakerP
"There are
@PressSec:
#TrumpLies
@MollyJong
#MoreTrump
Yikes. Inv
.@realDona
@realDonal
Our #Would
Americans:
.@realDona
@ReesusP @
@Gabeandth
.@Twitter 
Coincidenc
.@SpeakerP
@barefoots
Well said 
Wouldn't i
It's hard 
@RepRuther
@HouseGOP 
@RepRuther
@RepAndyBi
@RepAndyBi

@themattdi
@BryanDaws
@MattM0720
@atrupar B
@themattdi
@briebriej
@FennieDee
@mtracey U
@mtracey I
@trying2he
@TurtleMik
@GovJVentu
@Anita_Wah
@themattdi
@themattdi
@KachinMam
@BeatlesCa
@ggreenwal
@ggreenwal
@ggreenwal
@BeatlesCa
@lunadyana
@themattdi
@themattdi
@mtracey D
@JimThom20
@mtracey B
@SykesChar
@michaelwh
@4everNeve
@atrupar P
@billisbac
@atrupar W
@mtracey I
@girlyGRRR
@mtracey N
@themattdi
@RealMancr
@RealMancr
@RealMancr
@owenrumne
@ggreenwal
@ggreenwal
@mtracey Y
@mtracey A
@Wilson__V
@khmerradi
@realDonal
@mtracey W
@SonofDeca
@SonofDeca
@SonofDeca
@SonofDeca
@ControlCe
@SonofDeca
@ChrisNove
@ControlCe
#facepalm 
@mtracey Y
@mtracey T
@anashwt @
I also hav
@mtracey I
@ggreenwal
@ggreenwal
@sarahelab
@ggreenwal
@ggreenwal
@SkyNews I
@KingCharl
@RandPaul 
@KingCharl
@InigoMont
@TotallyHu
@LibertyIn
@ConnieSch
@mtracey W
@ABarnardN
@sifutweet
@jacobinma
@girlyGRRR
@QueenInYe
#IstandWit
@themattdi
@JayEllGii
Lord, keep
@WilliamTr
@GeorgeMor
@GeorgeMor
@ggreenwal
@themattdi

...

@CalebJHul
@realDonal
@McConnell
@IvankaTru
@PressSec 
@Lrihendry
@SexCounse
@realDonal
@thehill H
@thehill S
@realDonal
@WhiteHous
@realDonal
@USGLC @Iv
@realDonal
@RealMancr
@RealMancr
@realDonal
@USAinUAE 
@Ldyblkbd 
@IvankaTru
@realDonal
You are no
@JorgeFLor
@realDonal
@realDonal
@realDonal
@realDonal
@realDonal
@realDonal
@realDonal
@realDonal
@realDonal
@realDonal
@realDonal
@realDonal
@senatemaj
@alx @Dona
@thehill D
@RightWing
@IvankaTru
@WhiteHous
@JohnJames
@realDonal
@TeamTrump
@GOP @Ivan
@Acyn Mute
@photowhit
@WhiteHous
@LindseyGr
@NikkiHale
@SenCapito
@DonaldJTr
@realDonal
@realDonal
@DonaldJTr
@kimguilfo
@thehill W
@EricTrump
@LauraLMon
@LindseyGr
@SergioGor
@JonathanT
@WhiteHous
@IvankaTru
@marwillia
@IvankaTru
@EricTrump
@realDonal
@CLewandow
@rfhyde1 D
WTH is his
@DonaldJTr
@thehill T
@thehill N
@WhiteHous
@thehill A
@rfhyde1 S
@thehill @
@mmpadella
@WhiteHous
@RealSaave
@realDonal
@thehill @
@chuckwool
@WhiteHous
@EricTrump
@realDonal
@RandPaul 
@RudyGiuli
@thehill H

Also....Na
Two days t
Upcoming t
@RockySly9
@Mannybl2 
@spider196
@dewme Ava
@DreamWrit
@Hucksterd
Check out 
Have you b
@CraigHone
Which part
This is hi
What bette
Let’s part
@PhilipFra
@Samy_TheB
@iihave10t
Upcoming c
Just did t
@jeffgq @B
@BenTurn16
@lauriecro
@lauriecro
Can't wait
FLORIDA! S
@BraylenNa
Well....th
@salextodd
Let's do t
@Mrs_Mille
Upcoming s
@MclarenSa
Tweet of t
Thank you!
Thank you 
@ConradShe
@JaneDoe82
@KZzyzwicz
@chamblee5
Loving tha
@Riverra98
@Hazey0213
@Hazey0213
FLORIDA! S
Houston! W
Dallas! Jo
Chicago!! 
@Peter3072
@Rickfranc
@thetalent
@Yankeecow
@dropped_m
@dbkohl66 
@ElaineGas
All the fo
@Peter3072
Upcoming a
@jewpublic
See you so
@TommyIgoe
@Alt_Deadp
@TommyIgoe
Literally 
@DeiLauria
@DeiLauria
@PonyTheBo
@thebigdog
@d_m_t1023
@deK8sam @
@stevenson
@Comtigers
@FemdomCra
You can ch
@N_Y_N_E_R
@pegasus44
@JuJuJames
@JuJuJames
@plutonium
Depends wh
Enjoy! Rep
@pegasus44
I don't ne
@schavejon
Want me to
My new ful
I can now 
HOUSTON! I
Dallas! I 
@57wranny 

Me right n
Yas. https
Yes. https
👏 Fake 👏 N
Much neede
@gaywonk x
Let's all 
So many of
When your 
@tylersbug
Hate to sa
Current mo
@TheFlexas
Right now 
this is NO
So was inf
BUT CAN'T 
So to be c
🤔 https://
Something 
@gaywonk i
😂

🙃

😨

😰
How do we 
Who's the 
This is no
Chaffetz b
If Trump i
"Big" Luth
ASKING WHA
No time to
Look it's 
Spicer cal
If walking
@ClinicEsc
This admin
Guys thing
Honestly, 
HEY FANCY 
Everything
"I tried, 
@owillis t
Is it base
Superb Owl
This is wh
Hi hello i
Refuse to 
Hi it's Fr
If I reali
I spent SI
Not to out
I live in 
It's 3pm a
Cheering s
This admin
Muslims ar
Hi hello i
Williams/W
Steven Uni
@gaywonk W
This pictu
@gaywonk L
@gaywonk *
@gaywonk l
Bookmark. 
🔥 💅🏻 😭 htt
This is no
Even Ben C
Live shot 
I've alway
Super grea
👏 THIS 👏 I
Fmr POW ha
Can't wait
Masculinit
Donald Tru
Today's th
There's al
CNN made t
How many y
I adore @M
Great star
Listen to 
Some peopl
Where's As
The wicked
How fittin
Worth repe
Well, this
#WhiteMenC
With his p
Good on yo

@Chloe_Hil
@Gianmarco
@raylong09
@tashez He
@BrianLind
@BradLoekl
@RoryAlban
I wasn't t
@raesanni 
At this po
@Gianmarco
@RoryAlban
Co-Freakin
@iamwandas
✊🏾 https:/
🤣😅🤣😅🤣😅😅😅😅😅
@silkyjumb
@fashionsi
@darthman_
@chrismora
@curlycome
Black peop
Remember, 
Yall ready
@BradLoekl
True story
@BradLoekl
When the m
When the m
Watch my f
@SaraJBeni
Omg! How c
@DaWriter 
@DaWriter 
@blairsocc
You gonna 
COVID-19, 
@BradLoekl
@DaWriter 
Someone ju
@DaWriter 
Joe Biden 
I don't AF
#grits htt
@andimjust
#blackgran
@rilgood T
@daxDakota
@rilgood 🤗
I cant tha
@DarinCred
OJ is on #
@BradLoekl
Move over 
@TheBrownB
Good for @
@BrianLind
Yes, I'm s
For the re
Me: I'm do
@koconews

Dear Wack 
I'm at the
I wonder w
@TtSonny @
@katersgon
@JayJurden
@ShadedGli
@itsRoJay 
@TheBrownB
Just show 
@JamesEFin
I am thee 
This how I
Friend: WY
Just got a
When @miss
Never once
Ya'll can 
The scarie
This is #A
SMH https:
#Covid #Ka
@tanyaweim
Wow! Truth
Here's a l
@EricMadar
@EricMadar
@Galactic_
@BradLoekl
I saw a lo

I can mult
Good. I en
The Black 
Have you s
When did I
You are no
I'm sorry,
You're "te
Reply as i
When did I
@LqLana @M
@IronburrJ
Gay black 
I truly ap
You're ver
Explain wh
@Mxstr7 @Y
@IronburrJ
You're not
Gay people
Who is "us
No, he is 
Why do you
This is st
🙏🏾✊🏾 https
Nah I'm di
You don't 
Caption th
That's a g
What colle
You weren'
You're spe
You done l
Stop being
@TheOrigin
You're rac
You being 
Both of my
You're a r
This may b
So why are
There he i
Yea. You'r
So, are yo
You don't 
"Fuck head
Explain wh
Teaching w
Both of my
Saying "my
Did you te
So you agr
I'm in the
Telling yo
I looked. 
Not one me
My rap son
My art is 
TV writers
I mean I s
So now you
You have a
My thought
The actual
If I ask y
You didn't
He made a 
People jum
No. Did Co
No. Did Co
Which one 
I am a pro
I disagree
Actual act
@Robertthe
As I alrea
So hold up
I don't bu
So when Co
I already 
I disagree
Or, maybe 
So when Co
You seem t
So you mis
So because
J Cole is 
And? You k
I don't un
Dont Cole 
You ignore

In [41]:
len(tweet_list)

96405

In [42]:
tweet_string = '   ||   '.join(tweet_list)

In [43]:
processed_text = tweet_string.lower().replace('\r','').replace('%','').replace('(','').replace(')','').replace('*','').replace('/','').replace('\\','').replace('[','').replace(']','').replace('^','').replace('_','').replace('`','').replace('~','').replace('{','').replace('}','')
processed_text = re.sub(r'[^\x00-\x7f]',r'', processed_text)
chars = sorted(list(set(processed_text)))
print(chars)
print('total chars:', len(chars))
char_indices = dict((c, i) for i, c in enumerate(chars))
indices_char = dict((i, c) for i, c in enumerate(chars))

['\n', ' ', '!', '"', '#', '$', '&', "'", '+', ',', '-', '.', '0', '1', '2', '3', '4', '5', '6', '7', '8', '9', ':', ';', '=', '?', '@', 'a', 'b', 'c', 'd', 'e', 'f', 'g', 'h', 'i', 'j', 'k', 'l', 'm', 'n', 'o', 'p', 'q', 'r', 's', 't', 'u', 'v', 'w', 'x', 'y', 'z', '|']
total chars: 54


In [39]:
def on_epoch_end(epoch, _):
    # Function invoked at end of each epoch. Prints generated text.
    print('''                                                       
@@@@@@@@  @@@@@@@    @@@@@@    @@@@@@@  @@@  @@@  @@@  
@@@@@@@@  @@@@@@@@  @@@@@@@@  @@@@@@@@  @@@  @@@  @@@  
@@!       @@!  @@@  @@!  @@@  !@@       @@!  @@@  @@!  
!@!       !@!  @!@  !@!  @!@  !@!       !@!  @!@  !@   
@!!!:!    @!@@!@!   @!@  !@!  !@!       @!@!@!@!  @!@  
!!!!!:    !!@!!!    !@!  !!!  !!!       !!!@!!!!  !!!  
!!:       !!:       !!:  !!!  :!!       !!:  !!!       
:!:       :!:       :!:  !:!  :!:       :!:  !:!  :!:  
:: ::::   ::       ::::: ::   ::: :::  ::   :::   ::  
: :: ::    :         : :  :    :: :: :   :   : :  :::  
                                                ''')
    print('----- Generating text after Epoch: %d' % epoch)

    if epoch >=2 and epoch % 2 == 0:
        start_index = random.randint(0, len(processed_text) - maxlen - 1)
        for temperature in [1.0]:
            print('----- temperature:', temperature)

            generated = ''
            sentence = processed_text[start_index: start_index + maxlen]
            generated += sentence
            print('----- Generating with seed: "' + sentence + '"')
            sys.stdout.write(generated)

            for i in range(2000):
                x_pred = np.zeros((1, maxlen, len(chars)))
                for t, char in enumerate(sentence):
                    x_pred[0, t, char_indices[char]] = 1.

                preds = model.predict(x_pred, verbose=0)[0]
                next_index = sample(preds, temperature)
                next_char = indices_char[next_index]

                generated += next_char
                sentence = sentence[1:] + next_char

                sys.stdout.write(next_char)
                sys.stdout.flush()
            with open('../data/new_raw_generated_right_tweets.txt', "a+") as f:
                f.write(generated[maxlen:]+"\n")
            print()
    else:
        pass
    pass

In [37]:
# cut the text in semi-redundant sequences of maxlen characters
maxlen = 120
step = 1
sentences = []
next_chars = []
for i in range(0, len(processed_text) - maxlen, step):
    sentences.append(processed_text[i: i + maxlen])
    next_chars.append(processed_text[i + maxlen])

x = np.zeros((len(sentences), maxlen, len(chars)), dtype=np.bool)
y = np.zeros((len(sentences), len(chars)), dtype=np.bool)
for i, sentence in enumerate(sentences):
    for t, char in enumerate(sentence):
        x[i, t, char_indices[char]] = 1
    y[i, char_indices[next_chars[i]]] = 1

In [38]:
print('Build model...')
model = Sequential()
model.add(LSTM(256, input_shape=(maxlen, len(chars))))
#model.add(Dense(len(chars)*2, activation='softmax'))
model.add(Dropout(0.2))
model.add(Dense(len(chars), activation='softmax'))
optimizer = RMSprop(lr=0.02)
model.compile(loss='categorical_crossentropy', optimizer="adam")

Build model...


In [40]:
# Fit the model
print_callback = LambdaCallback(on_epoch_end=on_epoch_end)
print("fitting model")
model.fit(x, y,
        batch_size=256,
        epochs=20,
        callbacks=[print_callback])

fitting model
Train on 15041052 samples
Epoch 1/20
   15616/15041052 [..............................] - ETA: 35:19:39 - loss: 3.2508                                                       
@@@@@@@@  @@@@@@@    @@@@@@    @@@@@@@  @@@  @@@  @@@  
@@@@@@@@  @@@@@@@@  @@@@@@@@  @@@@@@@@  @@@  @@@  @@@  
@@!       @@!  @@@  @@!  @@@  !@@       @@!  @@@  @@!  
!@!       !@!  @!@  !@!  @!@  !@!       !@!  @!@  !@   
@!!!:!    @!@@!@!   @!@  !@!  !@!       @!@!@!@!  @!@  
!!!!!:    !!@!!!    !@!  !!!  !!!       !!!@!!!!  !!!  
!!:       !!:       !!:  !!!  :!!       !!:  !!!       
:!:       :!:       :!:  !:!  :!:       :!:  !:!  :!:  
:: ::::   ::       ::::: ::   ::: :::  ::   :::   ::  
: :: ::    :         : :  :    :: :: :   :   : :  :::  
                                                
----- Generating text after Epoch: 0


KeyboardInterrupt: 